## Introduction
<B>Battle of Cities- Where and what type of restaurants to open in Bangalore</B>
<br>Business Problem Statement</br>
<p>With an explosive growth in IT services industry since early 2000s, Bangalore have become a true cosmopolitan city where you tend to find a lot of people from different region and different culture. With the inflow of skilled manpower to the city, it has also witnessed a major growth in variety of businesses of all categories. The exercise is to find the type of restaurants across in Bangalore. This exercise will try to build a model to suggest a localtiy and the nature of the restaurants that can be targetted at </p>

# Data Requirement

<h3>

1. List of neighborhoods in Bangalore
2. Latitude and longitude coordinates of the neighborhood
3. Venue data particularly related to category of restaurants and the poupalrity

</h3>

# Sources of Data

<h3>

1. Wikipedia Bangalore Neighborhood locations
https://en.wikipedia.org/wiki/List_of_neighbourhoods_in_Bangalore
<br></br>

2. Geocoder Package for latitude and longitude coordinates<br>
<br></br>
3. Foursquare API venue data
</h3>

Before we get the data and start exploring it, let's download all the dependencies that we will need.

In [73]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes 
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes
import folium # map rendering library

from bs4 import BeautifulSoup # library to parse HTML and XML documents
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
import geocoder # to get coordinates

print('Libraries imported.')

Solving environment: ...working... done

# All requested packages already installed.

Solving environment: ...working... done

# All requested packages already installed.

Libraries imported.


<a id='item1'></a>

## 1. Download and Explore Dataset

We will download the data from the Wikipedia for the localities of Bangalore. 

In [74]:
data = requests.get("https://en.wikipedia.org/wiki/Category:Neighbourhoods_in_Bangalore").text
soup = BeautifulSoup(data, 'html.parser')
# create a list to store neighborhood data
neighborhoodList = []

In [75]:
# append the data into the list
for row in soup.find_all("div", class_="mw-category")[0].findAll("li"):
    neighborhoodList.append(row.text)

In [76]:
print(neighborhoodList)

['List of areas in Bangalore Cantonment', 'List of areas in Bengaluru Pete', 'List of neighbourhoods in Bangalore', 'Adugodi', 'Agara, Bangalore', 'Ananthnagar', 'Anjanapura', 'Arekere', 'Austin Town', 'Babusapalya', 'Bagalur, Bangalore Urban', 'Bahubalinagar', 'Banashankari', 'Banaswadi', 'Basavanagudi', 'Basaveshwaranagar', 'Bellandur', 'Bengaluru Pete', 'Bharathnagar', 'Bilekahalli', 'Bommanahalli', 'Bommasandra', 'Brookefield', 'BTM Layout', 'Byatarayanapura', 'Carmelaram', 'Chamrajpet', 'Chandapura', 'Chickpet', 'Chikkalasandra', 'Cooke Town', 'Cox Town, Bangalore', 'CV Raman Nagar', 'Dasarahalli', 'Devarachikkanahalli', 'Dollars Colony', 'Domlur', 'Ejipura', 'Electronic City', 'Fraser Town, Bangalore', 'Gandhi Bazaar', 'Gandhi Nagar, Bangalore', 'Gangamma Circle', 'Ganganagar, Bangalore', 'Garudacharpalya', 'Girinagar', 'Gottigere', 'Gowdanapalya', 'Hanumanthanagar, Bengaluru', 'HBR Layout', 'Hebbagodi', 'Hebbal', 'Hoodi', 'Horamavu', 'HSR Layout', 'Hulimavu', 'Immadihalli', 'Ind

In [77]:
# create a new DataFrame from the list
kl_df = pd.DataFrame({"Neighborhood": neighborhoodList})

# kl_df

In [78]:
kl_df=kl_df.iloc[3:]
kl_df

Neighborhood
3                                Adugodi
4                       Agara, Bangalore
5                            Ananthnagar
6                             Anjanapura
7                                Arekere
8                            Austin Town
9                            Babusapalya
10              Bagalur, Bangalore Urban
11                         Bahubalinagar
12                          Banashankari
13                             Banaswadi
14                          Basavanagudi
15                     Basaveshwaranagar
16                             Bellandur
17                        Bengaluru Pete
18                          Bharathnagar
19                           Bilekahalli
20                          Bommanahalli
21                           Bommasandra
22                           Brookefield
23                            BTM Layout
24                       Byatarayanapura
25                            Carmelaram
26                            Chamrajpet
27                            Chandapura
28                              Chickpet
29                        Chikkalasandra
30                            Cooke Town
31                   Cox Town, Bangalore
32                        CV Raman Nagar
33                           Dasarahalli
34                   Devarachikkanahalli
35                        Dollars Colony
36                                Domlur
37                               Ejipura
38                       Electronic City
39                Fraser Town, Bangalore
40                         Gandhi Bazaar
41               Gandhi Nagar, Bangalore
42                       Gangamma Circle
43                 Ganganagar, Bangalore
44                       Garudacharpalya
45                             Girinagar
46                             Gottigere
47                          Gowdanapalya
48            Hanumanthanagar, Bengaluru
49                            HBR Layout
50                             Hebbagodi
51                                Hebbal
52                                 Hoodi
53                              Horamavu
54                            HSR Layout
55                              Hulimavu
56                           Immadihalli
57                           Indiranagar
58                              Ittamadu
59                           J. P. Nagar
60                           Jakkasandra
61                                Jakkur
62                             Jalahalli
63                  Jayanagar, Bangalore
64                    Jeevanbheema Nagar
65                                Jigani
66                              Kadugodi
67                         Kaggadasapura
68                          Kalasipalyam
69                           Kalikanagar
70                               Kalkere
71                          Kalyan Nagar
72                         Kamakshipalya
73                          Kammanahalli
74                               Kengeri
75                           Kodigehalli
76                  Kodihalli, Bangalore
77                           Konanakunte
78                            Koppa gate
79                           Koramangala
80                      Krishnarajapuram
81                    Kumaraswamy Layout
82                          Kundalahalli
83                        Lingarajapuram
84                              Madiwala
85               Mahadevapura, Bangalore
86                    Mahalakshmi Layout
87                           Malleswaram
88                          Marathahalli
89                        Mariyannapalya
90                             Mathikere
91                           Milk Colony
92                Murphy Town, Bangalore
93                         Murugeshpalya
94                         Muthyalanagar
95                            Nagarbhavi
96                        Nandini Layout
97                          Nayandahalli
98                       Padmanabhanagar
99                     Palace Guttahalli
100       

#### Load and explore the data

In [79]:
# print the number of rows of the dataframe
kl_df.shape

(136, 1)

In [80]:
# define a function to get coordinates
def get_latlng(neighborhood):
    # initialize your variable to None
    lat_lng_coords = None
    # loop until you get the coordinates
    while(lat_lng_coords is None):
        g = geocoder.arcgis('{}, Bangalore, India'.format(neighborhood))
        lat_lng_coords = g.latlng
    return lat_lng_coords

Next, let's load the data.

In [81]:
# call the function to get the coordinates, store in a new list using list comprehension

coords = [ get_latlng(neighborhood) for neighborhood in kl_df["Neighborhood"].tolist() ]

In [82]:
coords

[[12.944020000000023, 77.60800000000006],
 [12.842830000000049, 77.48759000000007],
 [12.954080000000033, 77.54135000000008],
 [12.858110000000067, 77.55909000000008],
 [12.885680000000036, 77.59668000000005],
 [12.963480000000061, 77.61297000000008],
 [13.02753000000007, 77.65049000000005],
 [13.07728933897749, 77.65760586439058],
 [13.044710000000066, 77.55008000000004],
 [12.922310000000039, 77.56988000000007],
 [13.019646729517714, 77.65469401219607],
 [12.938980000000072, 77.57137000000006],
 [12.992220000000032, 77.53444000000007],
 [12.927350000000047, 77.67185000000006],
 [12.960530000000063, 77.64385000000004],
 [13.083010000000058, 77.54779000000008],
 [12.900090000000034, 77.60433000000006],
 [12.903080000000045, 77.62444000000005],
 [12.817530000000033, 77.67879000000005],
 [12.993330000000071, 77.66123000000005],
 [12.91488000000004, 77.61004000000008],
 [12.951940000000036, 77.54445000000004],
 [12.913110000000074, 77.71565000000004],
 [12.959697329772126, 77.571311610841

Let's take a quick look at the data.

In [83]:
# create temporary dataframe to populate the coordinates into Latitude and Longitude
df_coords = pd.DataFrame(coords, columns=['Latitude', 'Longitude'])

In [84]:
# merge the coordinates into the original dataframe
kl_df['Latitude'] = df_coords['Latitude']
kl_df['Longitude'] = df_coords['Longitude']

In [85]:
# check the neighborhoods and the coordinates
print(kl_df.shape)
kl_df.head()

(136, 3)


Neighborhood   Latitude  Longitude
3           Adugodi  12.858110  77.559090
4  Agara, Bangalore  12.885680  77.596680
5       Ananthnagar  12.963480  77.612970
6        Anjanapura  13.027530  77.650490
7           Arekere  13.077289  77.657606

<h4> Clean the data of the null values </h4>

In [86]:
kl_df = kl_df[kl_df['Latitude'].notna()]
kl_df = kl_df[kl_df['Longitude'].notna()]

<h4> Use the geolocator to get the latitiude and longitude of Bangalore </h4>

In [87]:
address = 'Bangalore', 'KA'

geolocator = Nominatim(user_agent="bl_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Bangalore City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Bangalore City are 12.9791198, 77.5912997.


#### Create a map of Bengaluru with neighborhoods superimposed on top.

In [88]:
# create map of Bangalore using latitude and longitude values
map_kl = folium.Map(location=[12.9791198, 77.5912997], zoom_start=11)

# add markers to map
for lat, lng, neighborhood in zip(kl_df['Latitude'], kl_df['Longitude'], kl_df['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_kl)  
    
map_kl

#### Define Foursquare Credentials and Version

#### Let's explore the first neighborhood in our dataframe.

In [89]:
CLIENT_ID = 'LZWINMULMP41AA3WIHAWK3UH4C2B5WANMIK1AFZVOTZL4AML' # your Foursquare ID
CLIENT_SECRET = 'SIR13CF04OS0UNTLLGT3GPZHPUG1XS1SRPHWK5WUSG5UFJ3X' # your Foursquare Secret
VERSION = '20180605'
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: LZWINMULMP41AA3WIHAWK3UH4C2B5WANMIK1AFZVOTZL4AML
CLIENT_SECRET:SIR13CF04OS0UNTLLGT3GPZHPUG1XS1SRPHWK5WUSG5UFJ3X


Get the neighborhood's name.

In [90]:
radius = 2000
LIMIT = 100

venues = []

for lat, long, neighborhood in zip(kl_df['Latitude'], kl_df['Longitude'], kl_df['Neighborhood']):
    
    # create the API request URL
    url = "https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}".format(
        CLIENT_ID,
        CLIENT_SECRET,
        VERSION,
        lat,
        long,
        radius, 
        LIMIT)
    
    # make the GET request
#     results = requests.get(url).json()["response"]['groups'][0]['items']
    results = requests.get(url).json()['response'].get('groups',[{}])[0].get('items', [])
    
    # return only relevant information for each nearby venue
    for venue in results:
        venues.append((
            neighborhood,
            lat, 
            long, 
            venue['venue']['name'], 
            venue['venue']['location']['lat'], 
            venue['venue']['location']['lng'],  
            venue['venue']['categories'][0]['name']))

In [91]:

# convert the venues list into a new DataFrame
venues_df = pd.DataFrame(venues)

# define the column names
venues_df.columns = ['Neighborhood', 'Latitude', 'Longitude', 'VenueName', 'VenueLatitude', 'VenueLongitude', 'VenueCategory']

print(venues_df.shape)
venues_df.head(10)

(6925, 7)


Neighborhood  Latitude  Longitude                       VenueName  \
0           Adugodi  12.85811   77.55909            capital club resorts   
1           Adugodi  12.85811   77.55909                   Axis Bank ATM   
2           Adugodi  12.85811   77.55909                   Axis Bank ATM   
3           Adugodi  12.85811   77.55909                        Baristra   
4  Agara, Bangalore  12.88568   77.59668  Decathlon Sports India Pvt Ltd   
5  Agara, Bangalore  12.88568   77.59668                        Swensens   
6  Agara, Bangalore  12.88568   77.59668               Natural Ice Cream   
7  Agara, Bangalore  12.88568   77.59668                       Cinepolis   
8  Agara, Bangalore  12.88568   77.59668                         Chavadi   
9  Agara, Bangalore  12.88568   77.59668                      Ingu Tengu   

   VenueLatitude  VenueLongitude            VenueCategory  
0      12.855979       77.555653                     Pool  
1      12.859010       77.569420                      ATM  
2      12.859010       77.569420                      ATM  
3      12.848037       77.568779              Coffee Shop  
4      12.887513       77.597712      Sporting Goods Shop  
5      12.876071       77.595542           Ice Cream Shop  
6      12.892188       77.598222           Ice Cream Shop  
7      12.876119       77.595455                Multiplex  
8      12.892199       77.602538                BBQ Joint  
9      12.883268       77.607514  South Indian Restaurant

In [92]:
venues_df.groupby(["Neighborhood"]).count()


Latitude  Longitude  VenueName  \
Neighborhood                                                          
Adugodi                                     4          4          4   
Agara, Bangalore                           80         80         80   
Ananthnagar                               100        100        100   
Anjanapura                                 48         48         48   
Arekere                                    10         10         10   
Austin Town                                23         23         23   
BTM Layout                                 78         78         78   
Babusapalya                               100        100        100   
Bagalur, Bangalore Urban                   54         54         54   
Bahubalinagar                             100        100        100   
Banashankari                               40         40         40   
Banaswadi                                  88         88         88   
Basavanagudi                              100        100        100   
Basaveshwaranagar                           7          7          7   
Bellandur                                  93         93         93   
Bengaluru Pete                             63         63         63   
Bharathnagar                                7          7          7   
Bilekahalli                                41         41         41   
Bommanahalli                               88         88         88   
Bommasandra                                31         31         31   
Brookefield                                 5          5          5   
Byatarayanapura                             4          4          4   
CV Raman Nagar                             66         66         66   
Carmelaram                                 70         70         70   
Chamrajpet                                 37         37         37   
Chandapura                                 73         73         73   
Chickpet                                   71         71         71   
Chikkalasandra                             99         99         99   
Cooke Town                                 24         24         24   
Cox Town, Bangalore                        19         19         19   
Dasarahalli                                47         47         47   
Devarachikkanahalli                        79         79         79   
Dollars Colony                             48         48         48   
Domlur                                     95         95         95   
Ejipura                                    98         98         98   
Electronic City                            21         21         21   
Fraser Town, Bangalore                      7          7          7   
Gandhi Bazaar                              75         75         75   
Gandhi Nagar, Bangalore                    78         78         78   
Gangamma Circle                            27         27         27   
Ganganagar, Bangalore                       7          7          7   
Garudacharpalya                            52         52         52   
Girinagar                                  76         76         76   
Gottigere                                  58         58         58   
Gowdanapalya                               15         15         15   
HBR Layout                                 45         45         45   
HSR Layout                                  8          8          8   
Hanumanthanagar, Bengaluru                 37         37         37   
Hebbagodi                                   4          4          4   
Hebbal                                     67         67         67   
Hoodi                                      62         62         62   
Horamavu                                   36         36         36   
Hulimavu                                   34         34         34   
Immadihalli                               100        100        100   
Indiranagar                               100        100     

In [93]:
print('There are {} uniques categories.'.format(len(venues_df['VenueCategory'].unique())))

There are 229 uniques categories.


Get the neighborhood's latitude and longitude values.

In [94]:
venues_df['VenueCategory'].unique()[:229] #Displays all the categories

array(['Pool', 'ATM', 'Coffee Shop', 'Sporting Goods Shop',
       'Ice Cream Shop', 'Multiplex', 'BBQ Joint',
       'South Indian Restaurant', 'Lounge', 'Indian Restaurant',
       'Bowling Alley', 'Beer Garden', 'Brewery', 'Pizza Place', 'Café',
       'Shopping Mall', 'Chinese Restaurant', 'Restaurant',
       'Department Store', 'Liquor Store', 'Office', 'Sandwich Place',
       'Fast Food Restaurant', 'Eastern European Restaurant',
       'Middle Eastern Restaurant', 'General Entertainment',
       'Burger Joint', 'American Restaurant', 'Rajasthani Restaurant',
       'Italian Restaurant', 'Supermarket', 'Dive Bar',
       'Dumpling Restaurant', 'Electronics Store', 'Clothing Store',
       'Movie Theater', 'Furniture / Home Store', 'Mexican Restaurant',
       'Taco Place', 'Breakfast Spot', 'Food Court',
       'Vegetarian / Vegan Restaurant', 'Bookstore', 'Bakery',
       'Grocery Store', 'Convenience Store', 'Pharmacy', 'Donut Shop',
       'Cocktail Bar', 'Soccer Stadium', '

In [95]:
# # one hot encoding
# kl_onehot = pd.get_dummies(venues_df[['VenueCategory']], prefix="", prefix_sep="")

# # add neighborhood column back to dataframe
# kl_onehot['Neighborhoods'] = venues_df['Neighborhood'] 

# # move neighborhood column to the first column
# fixed_columns = [kl_onehot.columns[-1]] + list(kl_onehot.columns[:-1])
# kl_onehot = kl_onehot[fixed_columns]

# print(kl_onehot.shape)
# kl_onehot.head(20)

# one hot encoding
kl_onehot = pd.get_dummies(venues_df[['VenueCategory']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
kl_onehot['Neighborhood'] = venues_df['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [kl_onehot.columns[-1]] + list(kl_onehot.columns[:-1])
kl_onehot = kl_onehot[fixed_columns]

kl_onehot.head()

Yoga Studio  ATM  Accessories Store  Afghan Restaurant  Airport  \
0            0    0                  0                  0        0   
1            0    1                  0                  0        0   
2            0    1                  0                  0        0   
3            0    0                  0                  0        0   
4            0    0                  0                  0        0   

   American Restaurant  Andhra Restaurant  Arcade  Art Gallery  Art Museum  \
0                    0                  0       0            0           0   
1                    0                  0       0            0           0   
2                    0                  0       0            0           0   
3                    0                  0       0            0           0   
4                    0                  0       0            0           0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0                    0                 0                   0   
1                    0                 0                   0   
2                    0                 0                   0   
3                    0                 0                   0   
4                    0                 0                   0   

   Australian Restaurant  Auto Garage  Auto Workshop  BBQ Joint  \
0                      0            0              0          0   
1                      0            0              0          0   
2                      0            0              0          0   
3                      0            0              0          0   
4                      0            0              0          0   

   Badminton Court  Bagel Shop  Bakery  Bar  Basketball Court  \
0                0           0       0    0                 0   
1                0           0       0    0                 0   
2                0           0       0    0                 0   
3                0           0       0    0                 0   
4                0           0       0    0                 0   

   Bed & Breakfast  Beer Bar  Beer Garden  Bengali Restaurant  Big Box Store  \
0                0         0            0                   0              0   
1                0         0            0                   0              0   
2                0         0            0                   0              0   
3                0         0            0                   0              0   
4                0         0            0                   0              0   

   Bike Shop  Bistro  Boarding House  Boat or Ferry  Bookstore  \
0          0       0               0              0          0   
1          0       0               0              0          0   
2          0       0               0              0          0   
3          0       0               0              0          0   
4          0       0               0              0          0   

   Botanical Garden  Boutique  Bowling Alley  Breakfast Spot  Brewery  Bridge  \
0                 0         0              0               0        0       0   
1                 0         0              0               0        0       0   
2                 0         0              0               0        0       0   
3                 0         0              0               0        0       0   
4                 0         0              0               0        0       0   

   Bubble Tea Shop  Building  Burger Joint  Burrito Place  Bus Line  \
0                0         0             0              0         0   
1                0         0             0              0         0   
2                0         0             0              0         0   
3                0         0             0              0         0   
4                0         0             0              0         0   

   Bus Station  Bus Stop  Butcher  Cafeteria  Café  Campground  Candy Store  \
0            0         0        0          0     0           0 

In [96]:
kl_grouped = kl_onehot.groupby('Neighborhood').mean().reset_index()
kl_grouped

Neighborhood  Yoga Studio       ATM  \
0                                Adugodi     0.000000  0.500000   
1                       Agara, Bangalore     0.000000  0.000000   
2                            Ananthnagar     0.000000  0.000000   
3                             Anjanapura     0.000000  0.000000   
4                                Arekere     0.000000  0.000000   
5                            Austin Town     0.000000  0.000000   
6                             BTM Layout     0.000000  0.000000   
7                            Babusapalya     0.000000  0.000000   
8               Bagalur, Bangalore Urban     0.000000  0.000000   
9                          Bahubalinagar     0.000000  0.000000   
10                          Banashankari     0.000000  0.000000   
11                             Banaswadi     0.000000  0.000000   
12                          Basavanagudi     0.000000  0.000000   
13                     Basaveshwaranagar     0.000000  0.000000   
14                             Bellandur     0.000000  0.000000   
15                        Bengaluru Pete     0.000000  0.000000   
16                          Bharathnagar     0.000000  0.000000   
17                           Bilekahalli     0.000000  0.000000   
18                          Bommanahalli     0.000000  0.000000   
19                           Bommasandra     0.000000  0.000000   
20                           Brookefield     0.000000  0.000000   
21                       Byatarayanapura     0.000000  0.000000   
22                        CV Raman Nagar     0.000000  0.000000   
23                            Carmelaram     0.000000  0.000000   
24                            Chamrajpet     0.000000  0.000000   
25                            Chandapura     0.000000  0.000000   
26                              Chickpet     0.000000  0.000000   
27                        Chikkalasandra     0.000000  0.000000   
28                            Cooke Town     0.000000  0.000000   
29                   Cox Town, Bangalore     0.000000  0.000000   
30                           Dasarahalli     0.000000  0.000000   
31                   Devarachikkanahalli     0.012658  0.000000   
32                        Dollars Colony     0.000000  0.000000   
33                                Domlur     0.000000  0.000000   
34                               Ejipura     0.000000  0.000000   
35                       Electronic City     0.000000  0.000000   
36                Fraser Town, Bangalore     0.000000  0.000000   
37                         Gandhi Bazaar     0.013333  0.000000   
38               Gandhi Nagar, Bangalore     0.000000  0.000000   
39                       Gangamma Circle     0.000000  0.000000   
40                 Ganganagar, Bangalore     0.000000  0.000000   
41                       Garudacharpalya     0.000000  0.000000   
42                             Girinagar     0.000000  0.000000   
43                             Gottigere     0.000000  0.000000   
44                          Gowdanapalya     0.000000  0.000000   
45                            HBR Layout     0.000000  0.000000   
46                            HSR Layout     0.000000  0.375000   
47            Hanumanthanagar, Bengaluru     0.000000  0.000000   
48                             Hebbagodi     0.000000  0.000000   
49                                Hebbal     0.000000  0.000000   
50                                 Hoodi     0.000000  0.000000   
51                              Horamavu     0.000000  0.000000   
52                              Hulimavu     0.000000  0.000000   
53                           Immadihalli     0.000000  0.000000   
54                           Indiranagar     0.000000  0.000000   
55                              Ittamadu     0.000000  0.000000   
56                           J. P. Nagar     0.000000  0.000000   
57                           Jakkasandra     0.000000  0.000000   
58                                Jakkur     0.000000  0.000000   
59      

In [97]:
kl_grouped = kl_onehot.groupby(["Neighborhood"]).sum().reset_index()
print(kl_grouped.shape)
kl_grouped

(133, 229)


Neighborhood  Yoga Studio  ATM  Accessories Store  \
0                                Adugodi            0    2                  0   
1                       Agara, Bangalore            0    0                  0   
2                            Ananthnagar            0    0                  0   
3                             Anjanapura            0    0                  0   
4                                Arekere            0    0                  0   
5                            Austin Town            0    0                  0   
6                             BTM Layout            0    0                  0   
7                            Babusapalya            0    0                  0   
8               Bagalur, Bangalore Urban            0    0                  0   
9                          Bahubalinagar            0    0                  0   
10                          Banashankari            0    0                  0   
11                             Banaswadi            0    0                  0   
12                          Basavanagudi            0    0                  0   
13                     Basaveshwaranagar            0    0                  0   
14                             Bellandur            0    0                  0   
15                        Bengaluru Pete            0    0                  0   
16                          Bharathnagar            0    0                  0   
17                           Bilekahalli            0    0                  0   
18                          Bommanahalli            0    0                  0   
19                           Bommasandra            0    0                  0   
20                           Brookefield            0    0                  0   
21                       Byatarayanapura            0    0                  0   
22                        CV Raman Nagar            0    0                  0   
23                            Carmelaram            0    0                  0   
24                            Chamrajpet            0    0                  0   
25                            Chandapura            0    0                  0   
26                              Chickpet            0    0                  0   
27                        Chikkalasandra            0    0                  0   
28                            Cooke Town            0    0                  0   
29                   Cox Town, Bangalore            0    0                  0   
30                           Dasarahalli            0    0                  0   
31                   Devarachikkanahalli            1    0                  0   
32                        Dollars Colony            0    0                  0   
33                                Domlur            0    0                  0   
34                               Ejipura            0    0                  0   
35                       Electronic City            0    0                  0   
36                Fraser Town, Bangalore            0    0                  0   
37                         Gandhi Bazaar            1    0                  0   
38               Gandhi Nagar, Bangalore            0    0                  0   
39                       Gangamma Circle            0    0                  0   
40                 Ganganagar, Bangalore            0    0                  0   
41                       Garudacharpalya            0    0                  0   
42                             Girinagar            0    0                  0   
43                             Gottigere            0    0                  0   
44                          Gowdanapalya            0    0                  0   
45                            HBR Layout            0    0                  0   
46                            HSR Layout            0    3                  0   
47            Hanumanthanagar, Bengaluru            0    0                  0   
48                             Hebbagodi            0    0 

<h4> Now we will find the top five venues for each locality by considering their frquency</h4>

In [98]:
num_top_venues = 5

for hood in kl_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = kl_grouped[kl_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Adugodi----
                            venue  freq
0                             ATM   2.0
1                            Pool   1.0
2                     Coffee Shop   1.0
3  Multicuisine Indian Restaurant   0.0
4                   Metro Station   0.0


----Agara, Bangalore----
                     venue  freq
0        Indian Restaurant  10.0
1                     Café   8.0
2           Ice Cream Shop   5.0
3              Pizza Place   4.0
4  South Indian Restaurant   3.0


----Ananthnagar----
               venue  freq
0              Hotel   9.0
1  Indian Restaurant   9.0
2                Pub   5.0
3     Ice Cream Shop   4.0
4               Café   4.0


----Anjanapura----
               venue  freq
0  Indian Restaurant   8.0
1  Korean Restaurant   3.0
2          BBQ Joint   3.0
3               Café   3.0
4     Ice Cream Shop   2.0


----Arekere----
                  venue  freq
0           Coffee Shop   1.0
1  Gym / Fitness Center   1.0
2           Pizza Place   1.0
3        Sandw

<h4>Now we will define a function to find the most common venues</h4>

In [99]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

<h4>Find the top 10 most  common venues </h4>

In [100]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = kl_grouped['Neighborhood']

for ind in np.arange(kl_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(kl_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0           Adugodi                   ATM           Coffee Shop   
1  Agara, Bangalore     Indian Restaurant                  Café   
2       Ananthnagar                 Hotel     Indian Restaurant   
3        Anjanapura     Indian Restaurant                  Café   
4           Arekere           Pizza Place               Brewery   

  3rd Most Common Venue 4th Most Common Venue     5th Most Common Venue  \
0                  Pool         Women's Store        Dim Sum Restaurant   
1        Ice Cream Shop           Pizza Place          Department Store   
2                   Pub                  Café            Ice Cream Shop   
3             BBQ Joint     Korean Restaurant               Coffee Shop   
4           Coffee Shop  Gym / Fitness Center  Mediterranean Restaurant   

     6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0           Farmers Market    Falafel Restaurant           Event Space   
1  South Indian Restaurant        Clothing Store  Fast Food Restaurant   
2                  Brewery              Tea Room                Lounge   
3                   Lounge    Chinese Restaurant  Fast Food Restaurant   
4        Convenience Store        Sandwich Place       Badminton Court   

  9th Most Common Venue 10th Most Common Venue  
0         Event Service      Electronics Store  
1         Shopping Mall     Chinese Restaurant  
2                   Bar         Breakfast Spot  
3           Pizza Place         Ice Cream Shop  
4   Sporting Goods Shop                Stadium

<h4> Listing the top 10 most common venues for all the locality</h4>

In [101]:
neighborhoods_venues_sorted

Neighborhood   1st Most Common Venue  \
0                                Adugodi                     ATM   
1                       Agara, Bangalore       Indian Restaurant   
2                            Ananthnagar                   Hotel   
3                             Anjanapura       Indian Restaurant   
4                                Arekere             Pizza Place   
5                            Austin Town       Indian Restaurant   
6                             BTM Layout       Indian Restaurant   
7                            Babusapalya       Indian Restaurant   
8               Bagalur, Bangalore Urban       Indian Restaurant   
9                          Bahubalinagar       Indian Restaurant   
10                          Banashankari       Indian Restaurant   
11                             Banaswadi       Indian Restaurant   
12                          Basavanagudi       Indian Restaurant   
13                     Basaveshwaranagar             Coffee Shop   
14                             Bellandur       Indian Restaurant   
15                        Bengaluru Pete       Indian Restaurant   
16                          Bharathnagar                   Hotel   
17                           Bilekahalli       Indian Restaurant   
18                          Bommanahalli       Indian Restaurant   
19                           Bommasandra       Indian Restaurant   
20                           Brookefield            Soccer Field   
21                       Byatarayanapura       Indian Restaurant   
22                        CV Raman Nagar       Indian Restaurant   
23                            Carmelaram       Indian Restaurant   
24                            Chamrajpet                    Café   
25                            Chandapura       Indian Restaurant   
26                              Chickpet       Indian Restaurant   
27                        Chikkalasandra       Indian Restaurant   
28                            Cooke Town       Indian Restaurant   
29                   Cox Town, Bangalore       Indian Restaurant   
30                           Dasarahalli                    Café   
31                   Devarachikkanahalli       Indian Restaurant   
32                        Dollars Colony       Indian Restaurant   
33                                Domlur       Indian Restaurant   
34                               Ejipura       Indian Restaurant   
35                       Electronic City       Indian Restaurant   
36                Fraser Town, Bangalore      Italian Restaurant   
37                         Gandhi Bazaar       Indian Restaurant   
38               Gandhi Nagar, Bangalore             Coffee Shop   
39                       Gangamma Circle       Indian Restaurant   
40                 Ganganagar, Bangalore       Indian Restaurant   
41                       Garudacharpalya             Pizza Place   
42                             Girinagar       Indian Restaurant   
43                             Gottigere       Indian Restaurant   
44                          Gowdanapalya                   Hotel   
45                            HBR Layout       Indian Restaurant   
46                            HSR Layout                     ATM   
47            Hanumanthanagar, Bengaluru       Indian Restaurant   
48                             Hebbagodi        Department Store   
49                                Hebbal       Indian Restaurant   
50                                 Hoodi       Indian Restaurant   
51                              Horamavu                    Café   
52                              Hulimavu       Indian Restaurant   
53                           Immadihalli       Indian Restaurant   
54                           Indiranagar       Indian Restaurant   
55                              Ittamadu       Indian Restaurant   
56                           J. P. Nagar    Fast Food Restaurant   
57                           Jakkasandra       Indian Restaurant   
58              

## Creating a model using Cluster Analysis for all the services in Localities across Bangalore

<h4> This is my first step to analyse the localties depending on the number of services</h4>

In [102]:
# set number of clusters
kclusters = 5

kl_grouped_clustering = kl_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(kl_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([1, 0, 4, 0, 1, 1, 2, 2, 0, 2])

In [103]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels 3', kmeans.labels_)

kl_merged = kl_df

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
kl_merged = kl_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

kl_merged.head() # check the last columns!

Neighborhood   Latitude  Longitude  Cluster Labels 3  \
3           Adugodi  12.858110  77.559090                 1   
4  Agara, Bangalore  12.885680  77.596680                 0   
5       Ananthnagar  12.963480  77.612970                 4   
6        Anjanapura  13.027530  77.650490                 0   
7           Arekere  13.077289  77.657606                 1   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
3                   ATM           Coffee Shop                  Pool   
4     Indian Restaurant                  Café        Ice Cream Shop   
5                 Hotel     Indian Restaurant                   Pub   
6     Indian Restaurant                  Café             BBQ Joint   
7           Pizza Place               Brewery           Coffee Shop   

  4th Most Common Venue     5th Most Common Venue    6th Most Common Venue  \
3         Women's Store        Dim Sum Restaurant           Farmers Market   
4           Pizza Place          Department Store  South Indian Restaurant   
5                  Café            Ice Cream Shop                  Brewery   
6     Korean Restaurant               Coffee Shop                   Lounge   
7  Gym / Fitness Center  Mediterranean Restaurant        Convenience Store   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
3    Falafel Restaurant           Event Space         Event Service   
4        Clothing Store  Fast Food Restaurant         Shopping Mall   
5              Tea Room                Lounge                   Bar   
6    Chinese Restaurant  Fast Food Restaurant           Pizza Place   
7        Sandwich Place       Badminton Court   Sporting Goods Shop   

  10th Most Common Venue  
3      Electronics Store  
4     Chinese Restaurant  
5         Breakfast Spot  
6         Ice Cream Shop  
7                Stadium

In [105]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(kl_merged['Latitude'], kl_merged['Longitude'], kl_merged['Neighborhood'], kl_merged['Cluster Labels 3']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [106]:
k2=kl_merged

In [107]:
#kl_merged.loc[kl_merged['Cluster Labels 2'] == 0, kl_merged.columns[[1] + list(range(5, kl_merged.shape[1]))]]

In [108]:
k2.loc[k2['Cluster Labels 3'] == 0, k2.columns[[0] + list(range(5, k2.shape[1]))]]

Neighborhood 2nd Most Common Venue  \
4                       Agara, Bangalore                  Café   
6                             Anjanapura                  Café   
10              Bagalur, Bangalore Urban                  Café   
12                          Banashankari                  Café   
13                             Banaswadi                  Café   
19                           Bilekahalli                  Café   
33                           Dasarahalli  Fast Food Restaurant   
35                        Dollars Colony           Coffee Shop   
41               Gandhi Nagar, Bangalore                  Café   
44                       Garudacharpalya  Fast Food Restaurant   
46                             Gottigere                  Café   
48            Hanumanthanagar, Bengaluru        Ice Cream Shop   
52                                 Hoodi                  Café   
55                              Hulimavu                  Café   
70                               Kalkere                Bakery   
82                          Kundalahalli                  Café   
84                              Madiwala           Coffee Shop   
93                         Murugeshpalya        Clothing Store   
99                     Palace Guttahalli  Fast Food Restaurant   
100                               Peenya                  Café   
108                     Ramanjaneyanagar        Ice Cream Shop   
111                       Sahakara Nagar                 Hotel   
113                        Seshadripuram           Pizza Place   
119  Statue of Queen Victoria, Bangalore                  Café   
129                        Vasanth Nagar           Pizza Place   
131               Vijayanagar, Bangalore     Indian Restaurant   
132                           Vimanapura                  Café   
133                           Vyalikaval                  Café   

    3rd Most Common Venue          4th Most Common Venue  \
4          Ice Cream Shop                    Pizza Place   
6               BBQ Joint              Korean Restaurant   
10      Korean Restaurant                      BBQ Joint   
12   Fast Food Restaurant                 Ice Cream Shop   
13                  Hotel           Fast Food Restaurant   
19            Coffee Shop                    Pizza Place   
33      Indian Restaurant                          Hotel   
35                   Café                          Hotel   
41         Clothing Store           Fast Food Restaurant   
44                   Café              Indian Restaurant   
46   Fast Food Restaurant                    Pizza Place   
48       Department Store                    Pizza Place   
52         Ice Cream Shop               Department Store   
55            Pizza Place           Fast Food Restaurant   
70   Fast Food Restaurant                           Café   
82            Pizza Place                    Coffee Shop   
84     Italian Restaurant                 Clothing Store   
93                   Café             Italian Restaurant   
99            Bus Station  Vegetarian / Vegan Restaurant   
100  Fast Food Restaurant             Italian Restaurant   
108           Pizza Place           Fast Food Restaurant   
111  Fast Food Restaurant                    Coffee Shop   
113                  Café                  Shopping Mall   
119        Ice Cream Shop             Chinese Restaurant   
129                  Café                    Coffee Shop   
131  Fast Food Restaurant                           Café   
132                 Hotel                           Park   
133        Ice Cream Shop                 Breakfast Spot   

             5th Most Common Venue    6th Most Common Venue  \
4                 Department Store  South Indian Restaurant   
6                      Coffee Shop                   Lounge   
10                Department Store                   Bistro   
12                     Bus Station              Pizza Place   
13                     Coffee Shop                   Loun

In [68]:
k2.loc[k2['Cluster Labels 3'] == 1, k2.columns[[0] + list(range(5, k2.shape[1]))]]


Neighborhood   1st Most Common Venue  \
3                            Adugodi                     ATM   
7                            Arekere             Pizza Place   
8                        Austin Town       Indian Restaurant   
15                 Basaveshwaranagar             Coffee Shop   
18                      Bharathnagar                   Hotel   
21                       Bommasandra       Indian Restaurant   
22                       Brookefield            Soccer Field   
24                   Byatarayanapura       Indian Restaurant   
26                        Chamrajpet                    Café   
30                        Cooke Town       Indian Restaurant   
31               Cox Town, Bangalore       Indian Restaurant   
38                   Electronic City       Indian Restaurant   
39            Fraser Town, Bangalore      Italian Restaurant   
42                   Gangamma Circle       Indian Restaurant   
43             Ganganagar, Bangalore       Indian Restaurant   
47                      Gowdanapalya                   Hotel   
49                        HBR Layout       Indian Restaurant   
50                         Hebbagodi        Department Store   
53                          Horamavu                    Café   
54                        HSR Layout                     ATM   
58                          Ittamadu       Indian Restaurant   
59                       J. P. Nagar    Fast Food Restaurant   
62                         Jalahalli       Indian Restaurant   
63              Jayanagar, Bangalore                   Plaza   
66                          Kadugodi                     ATM   
67                     Kaggadasapura      Chinese Restaurant   
68                      Kalasipalyam       Indian Restaurant   
69                       Kalikanagar       Indian Restaurant   
71                      Kalyan Nagar       Indian Restaurant   
72                     Kamakshipalya          Ice Cream Shop   
74                           Kengeri       Indian Restaurant   
75                       Kodigehalli                     ATM   
77                       Konanakunte    Fast Food Restaurant   
78                        Koppa gate        Department Store   
83                    Lingarajapuram      Italian Restaurant   
86                Mahalakshmi Layout       Indian Restaurant   
91                       Milk Colony       Indian Restaurant   
92            Murphy Town, Bangalore       Indian Restaurant   
94                     Muthyalanagar             Pizza Place   
97                      Nayandahalli        Department Store   
101                     Puttenahalli             Pizza Place   
102                      R. T. Nagar       Indian Restaurant   
103                      Rajajinagar                     ATM   
104  Rajarajeshwari Nagar, Bangalore        Department Store   
105                  Ramachandrapura             Pizza Place   
114                     Shikaripalya       Indian Restaurant   
118  Statue of Edward VII, Bangalore  Furniture / Home Store   
121                        Sulikunte             Coffee Shop   
124                          Thindlu       Indian Restaurant   
125                  Thyagarajanagar             Pizza Place   
127                      Uttarahalli             Coffee Shop   
128                          Varthur         Badminton Court   
130                   Vidyaranyapura             Pizza Place   
134            Whitefield, Bangalore                    Café   
135                    Wilson Garden           Train Station   

    2nd Most Common Venue          3rd Most Common Venue  \
3             Coffee Shop                           Pool   
7                 Brewery                    Coffee Shop   
8          Ice Cream Shop             Punjabi Restaurant   
15            Pizza Place               Department Store   
18                   Café                    Coffee Shop   
21   Fast Food Restaurant                    Coffee Shop   
22    Sporting Good

In [109]:
k2.loc[k2['Cluster Labels 3'] == 2, k2.columns[[0] + list(range(5, k2.shape[1]))]]


Neighborhood 2nd Most Common Venue 3rd Most Common Venue  \
9       Babusapalya        Ice Cream Shop                  Café   
11    Bahubalinagar        Ice Cream Shop  Fast Food Restaurant   
20     Bommanahalli  Fast Food Restaurant        Ice Cream Shop   
23       BTM Layout  Fast Food Restaurant        Ice Cream Shop   
25       Carmelaram                 Hotel           Coffee Shop   
36           Domlur                  Café        Clothing Store   
37          Ejipura  Fast Food Restaurant                  Park   
45        Girinagar  Fast Food Restaurant        Breakfast Spot   
60      Jakkasandra        Ice Cream Shop                  Café   
65           Jigani  Fast Food Restaurant        Ice Cream Shop   
96   Nandini Layout           Coffee Shop                 Hotel   
110  Sadashivanagar                 Hotel           Coffee Shop   
122    Tannery Road        Ice Cream Shop           Coffee Shop   
126          Ulsoor                 Hotel        Ice Cream Shop   

    4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
9    Fast Food Restaurant           Coffee Shop    Chinese Restaurant   
11         Sandwich Place                  Café             Juice Bar   
20            Snack Place           Coffee Shop                Bakery   
23                 Bakery           Coffee Shop        Sandwich Place   
25   Fast Food Restaurant               Theater        Breakfast Spot   
36   Fast Food Restaurant             Juice Bar    Chinese Restaurant   
37                   Café        Sandwich Place           Coffee Shop   
45                   Café           Snack Place           Coffee Shop   
60   Fast Food Restaurant           Coffee Shop    Chinese Restaurant   
65            Coffee Shop                  Park                 Hotel   
96         Ice Cream Shop    Chinese Restaurant                  Café   
110    Chinese Restaurant          Dessert Shop  Fast Food Restaurant   
122                  Café  Fast Food Restaurant        Sandwich Place   
126           Coffee Shop          Dessert Shop    Chinese Restaurant   

         7th Most Common Venue          8th Most Common Venue  \
9                  Pizza Place        South Indian Restaurant   
11                 Snack Place                    Coffee Shop   
20                       Diner  Vegetarian / Vegan Restaurant   
23               Movie Theater               Asian Restaurant   
25          Seafood Restaurant  Vegetarian / Vegan Restaurant   
36   Middle Eastern Restaurant                         Bakery   
37                   Juice Bar                    Snack Place   
45              Sandwich Place                           Park   
60                   Juice Bar        South Indian Restaurant   
65                      Bakery                   Dessert Shop   
96        Fast Food Restaurant           Karnataka Restaurant   
110             Ice Cream Shop                            Pub   
122             Breakfast Spot                    Snack Place   
126                       Café               Department Store   

    9th Most Common Venue   10th Most Common Venue  
9      Italian Restaurant           Breakfast Spot  
11                   Park              Pizza Place  
20                    Gym           Sandwich Place  
23                  Hotel               Restaurant  
25              Juice Bar  South Indian Restaurant  
36         Ice Cream Shop                 Tea Room  
37         Ice Cream Shop           Breakfast Spot  
45             Restaurant         Department Store  
60            Snack Place           Sandwich Place  
65                Theater            Movie Theater  
96         Breakfast Spot                Juice Bar  
110             Nightclub       Seafood Restaurant  
122           Pizza Place               Restaurant  
126            Restaurant                      Pub

In [70]:
k2.loc[k2['Cluster Labels 3'] == 3, k2.columns[[0] + list(range(5, k2.shape[1]))]]


Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
16                 Bellandur     Indian Restaurant        Ice Cream Shop   
17            Bengaluru Pete     Indian Restaurant        Ice Cream Shop   
27                Chandapura     Indian Restaurant                  Café   
28                  Chickpet     Indian Restaurant                  Café   
29            Chikkalasandra     Indian Restaurant                  Café   
32            CV Raman Nagar     Indian Restaurant        Ice Cream Shop   
34       Devarachikkanahalli     Indian Restaurant                  Café   
40             Gandhi Bazaar     Indian Restaurant                  Café   
51                    Hebbal     Indian Restaurant                  Café   
56               Immadihalli     Indian Restaurant    Chinese Restaurant   
57               Indiranagar     Indian Restaurant                  Café   
64        Jeevanbheema Nagar     Indian Restaurant  Fast Food Restaurant   
76      Kodihalli, Bangalore     Indian Restaurant                  Café   
79               Koramangala     Indian Restaurant                  Café   
80          Krishnarajapuram     Indian Restaurant  Fast Food Restaurant   
81        Kumaraswamy Layout     Indian Restaurant                  Café   
85   Mahadevapura, Bangalore     Indian Restaurant           Pizza Place   
87               Malleswaram     Indian Restaurant        Ice Cream Shop   
88              Marathahalli     Indian Restaurant  Fast Food Restaurant   
95                Nagarbhavi     Indian Restaurant                  Café   
98           Padmanabhanagar     Indian Restaurant    Chinese Restaurant   
107         Ramamurthy Nagar     Indian Restaurant        Ice Cream Shop   
109            Richmond Town     Indian Restaurant        Ice Cream Shop   
117              Singasandra     Indian Restaurant                  Café   
120          Suddaguntepalya     Indian Restaurant                  Café   

    3rd Most Common Venue          4th Most Common Venue  \
16            Coffee Shop             Chinese Restaurant   
17            Pizza Place  Vegetarian / Vegan Restaurant   
27   Fast Food Restaurant                         Bakery   
28   Fast Food Restaurant                            Pub   
29         Ice Cream Shop                            Pub   
32   Fast Food Restaurant             Chinese Restaurant   
34              Juice Bar                 Breakfast Spot   
40   Fast Food Restaurant                    Coffee Shop   
51            Pizza Place                 Ice Cream Shop   
56            Coffee Shop                    Snack Place   
57         Ice Cream Shop                    Pizza Place   
64       Department Store                     Food Truck   
76         Ice Cream Shop           Fast Food Restaurant   
79            Pizza Place           Fast Food Restaurant   
80                 Bakery                           Café   
81         Ice Cream Shop                         Bakery   
85   Fast Food Restaurant                      BBQ Joint   
87   Fast Food Restaurant             Chinese Restaurant   
88         Ice Cream Shop                           Café   
95         Ice Cream Shop           Fast Food Restaurant   
98            Pizza Place                           Café   
107  Fast Food Restaurant                    Pizza Place   
109  Fast Food Restaurant             Chinese Restaurant   
117        Ice Cream Shop                    Coffee Shop   
120        Ice Cream Shop                   Dessert Shop   

             5th Most Common Venue      6th Most Common Venue  \
16                          Bakery                Pizza Place   
17                            Café           Department Store   
27                  Ice Cream Shop  Middle Eastern Restaurant   
28              Chinese Restaurant  Middle Eastern Restaurant   
29            Fast Food Restaurant                     Bakery   
32              Italian Restaurant                Pizza Place   
34                     

In [110]:
k2.loc[k2['Cluster Labels 3'] == 4, k2.columns[[0] + list(range(5, k2.shape[1]))]]


Neighborhood 2nd Most Common Venue 3rd Most Common Venue  \
5                Ananthnagar     Indian Restaurant                   Pub   
14              Basavanagudi            Restaurant                   Pub   
61                    Jakkur                  Café                   Pub   
73              Kammanahalli        Ice Cream Shop                  Café   
89            Mariyannapalya                  Café                   Pub   
90                 Mathikere            Restaurant                  Café   
106         Ramagondanahalli                Lounge                 Hotel   
112              Sanjaynagar        Clothing Store                 Hotel   
115  Shivajinagar, Bangalore                 Hotel                Lounge   
116     Siddapura, Bangalore            Restaurant        Ice Cream Shop   
123               Taverekere                  Café    Chinese Restaurant   

    4th Most Common Venue 5th Most Common Venue      6th Most Common Venue  \
5                    Café        Ice Cream Shop                    Brewery   
14         Ice Cream Shop                Lounge                        Bar   
61                    Bar                Lounge                 Restaurant   
73                    Pub            Restaurant                        Bar   
89             Restaurant        Clothing Store                      Hotel   
90                  Hotel                   Pub             Ice Cream Shop   
106                   Pub               Brewery                       Café   
112                  Café                Lounge             Ice Cream Shop   
115        Breakfast Spot                  Café                        Pub   
116                   Pub                  Café                Pizza Place   
123                   Pub                   Bar  Middle Eastern Restaurant   

    7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
5                Tea Room                Lounge                   Bar   
14                  Hotel              Tea Room    Chinese Restaurant   
61         Ice Cream Shop    Italian Restaurant          Cocktail Bar   
73       Asian Restaurant                Lounge          Cocktail Bar   
89         Ice Cream Shop      Department Store              Tea Room   
90   Fast Food Restaurant                   Bar             BBQ Joint   
106        Breakfast Spot    Chinese Restaurant    Italian Restaurant   
112                   Pub              Tea Room    Chinese Restaurant   
115                  Park   Japanese Restaurant    Italian Restaurant   
116                Bakery                 Hotel      Asian Restaurant   
123             BBQ Joint      Department Store           Coffee Shop   

    10th Most Common Venue  
5           Breakfast Spot  
14        Asian Restaurant  
61            Cupcake Shop  
73                 Brewery  
89                 Brewery  
90            Burger Joint  
106                    Gym  
112           Dessert Shop  
115       Sushi Restaurant  
116                    Bar  
123                  Hotel

## Explore the neighborhoods for the Vegan restaurants

In [111]:
len((kl_grouped[kl_grouped["Vegetarian / Vegan Restaurant"] > 0]))  #So there are  55 vegan restaurant in Bangalore (which it very high)
#So now we want to select a good location where the no of shopping malls are less so that our chances of setting up a shopping mall at that location  should be good

55

In [112]:
kl_vegan = kl_grouped[["Neighborhood","Vegetarian / Vegan Restaurant"]]
kl_vegan=kl_vegan[kl_vegan['Vegetarian / Vegan Restaurant']!=0]
kl_vegan.sort_values(['Vegetarian / Vegan Restaurant'], ascending=False)


Neighborhood  Vegetarian / Vegan Restaurant
81                   Madiwala                              4
97                     Peenya                              4
76                Koramangala                              3
18               Bommanahalli                              3
96          Palace Guttahalli                              3
104          Ramamurthy Nagar                              3
37              Gandhi Bazaar                              3
85               Marathahalli                              3
15             Bengaluru Pete                              3
14                  Bellandur                              3
78         Kumaraswamy Layout                              2
129                Vimanapura                              2
62                     Jigani                              2
93             Nandini Layout                              2
123                    Ulsoor                              2
52                   Hulimavu                              2
103          Ramagondanahalli                              2
80             Lingarajapuram                              2
73       Kodihalli, Bangalore                              2
107            Sadashivanagar                              2
112   Shivajinagar, Bangalore                              2
82    Mahadevapura, Bangalore                              2
23                 Carmelaram                              2
95            Padmanabhanagar                              2
130                Vyalikaval                              1
90              Murugeshpalya                              1
99                R. T. Nagar                              1
127            Vidyaranyapura                              1
125                   Varthur                              1
87                  Mathikere                              1
110             Seshadripuram                              1
113      Siddapura, Bangalore                              1
117           Suddaguntepalya                              1
106             Richmond Town                              1
1            Agara, Bangalore                              1
83         Mahalakshmi Layout                              1
3                  Anjanapura                              1
6                  BTM Layout                              1
8    Bagalur, Bangalore Urban                              1
9               Bahubalinagar                              1
11                  Banaswadi                              1
19                Bommasandra                              1
32             Dollars Colony                              1
34                    Ejipura                              1
35            Electronic City                              1
38    Gandhi Nagar, Bangalore                              1
39            Gangamma Circle                              1
42                  Girinagar                              1
43                  Gottigere                              1
45                 HBR Layout                              1
54                Indiranagar                              1
60       Jayanagar, Bangalore                              1
67                    Kalkere                              1
71                    Kengeri                              1
131     Whitefield, Bangalore                              1

In [113]:
# set number of clusters
kclusters = 4

kl_clustering = kl_vegan.drop(["Neighborhood"], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(kl_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([1, 1, 1, 1, 1, 1, 2, 2, 2, 1])

In [114]:
# create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.
kl_merged = kl_vegan.copy()

# add clustering labels
kl_merged["Cluster Labels"] = kmeans.labels_

In [115]:
kl_merged.rename(columns={"Neighborhoods": "Neighborhood"}, inplace=True)
kl_merged.head(10)

Neighborhood  Vegetarian / Vegan Restaurant  Cluster Labels
1           Agara, Bangalore                              1               1
3                 Anjanapura                              1               1
6                 BTM Layout                              1               1
8   Bagalur, Bangalore Urban                              1               1
9              Bahubalinagar                              1               1
11                 Banaswadi                              1               1
14                 Bellandur                              3               2
15            Bengaluru Pete                              3               2
18              Bommanahalli                              3               2
19               Bommasandra                              1               1

In [116]:
#Add latitude and longitude values by using the join operation(the new dataframe with the old dataframe containing the latitude and longitude values)
#kl_merged = kl_merged.join(kl_df.set_index("Neighborhood"), on="Neighborhood")

#print(kl_merged.shape)
kl_merged['Latitude'] = df_coords['Latitude']
kl_merged['Longitude'] = df_coords['Longitude']
kl_merged.head() # check the last columns!

Neighborhood  Vegetarian / Vegan Restaurant  Cluster Labels  \
1          Agara, Bangalore                              1               1   
3                Anjanapura                              1               1   
6                BTM Layout                              1               1   
8  Bagalur, Bangalore Urban                              1               1   
9             Bahubalinagar                              1               1   

   Latitude  Longitude  
1  12.84283   77.48759  
3  12.85811   77.55909  
6  13.02753   77.65049  
8  13.04471   77.55008  
9  12.92231   77.56988

<a id='item2'></a>

In [117]:
# sorting the results by Cluster Labels
print(kl_merged.shape)
kl_merged.sort_values(["Cluster Labels"], inplace=True)
kl_merged

(55, 5)


Neighborhood  Vegetarian / Vegan Restaurant  Cluster Labels  \
103          Ramagondanahalli                              2               0   
62                     Jigani                              2               0   
78         Kumaraswamy Layout                              2               0   
80             Lingarajapuram                              2               0   
52                   Hulimavu                              2               0   
82    Mahadevapura, Bangalore                              2               0   
93             Nandini Layout                              2               0   
95            Padmanabhanagar                              2               0   
23                 Carmelaram                              2               0   
73       Kodihalli, Bangalore                              2               0   
112   Shivajinagar, Bangalore                              2               0   
123                    Ulsoor                              2               0   
129                Vimanapura                              2               0   
107            Sadashivanagar                              2               0   
110             Seshadripuram                              1               1   
106             Richmond Town                              1               1   
130                Vyalikaval                              1               1   
99                R. T. Nagar                              1               1   
113      Siddapura, Bangalore                              1               1   
90              Murugeshpalya                              1               1   
87                  Mathikere                              1               1   
83         Mahalakshmi Layout                              1               1   
117           Suddaguntepalya                              1               1   
125                   Varthur                              1               1   
127            Vidyaranyapura                              1               1   
1            Agara, Bangalore                              1               1   
131     Whitefield, Bangalore                              1               1   
67                    Kalkere                              1               1   
3                  Anjanapura                              1               1   
6                  BTM Layout                              1               1   
8    Bagalur, Bangalore Urban                              1               1   
9               Bahubalinagar                              1               1   
11                  Banaswadi                              1               1   
19                Bommasandra                              1               1   
32             Dollars Colony                              1               1   
34                    Ejipura                              1               1   
71                    Kengeri                              1               1   
35            Electronic City                              1               1   
60       Jayanagar, Bangalore                              1               1   
38    Gandhi Nagar, Bangalore                              1               1   
39            Gangamma Circle                              1               1   
54                Indiranagar                              1               1   
42                  Girinagar                              1               1   
45                 HBR Layout                              1               1   
43                  Gottigere                              1               1   
96          Palace Guttahalli                              3               2   
14                  Bellandur                              3               2   
15             Bengaluru Pete                              3               2   
18               Bommanahalli                              3               2   
85               

## Visualize the clusters

In [118]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(kl_merged['Latitude'], kl_merged['Longitude'], kl_merged['Neighborhood'], kl_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

<a id='item5'></a>

## Examine Clusters

Now, you can examine each cluster and determine the discriminating venue categories that distinguish each cluster. Based on the defining categories, you can then assign a name to each cluster. 

#### Cluster 1

In [119]:
kl_merged.loc[kl_merged['Cluster Labels'] == 0]
#len(kl_merged.loc[kl_merged['Cluster Labels'] == 0])# -132 neighbourhoods/places in this cluster 0

Neighborhood  Vegetarian / Vegan Restaurant  Cluster Labels  \
103         Ramagondanahalli                              2               0   
62                    Jigani                              2               0   
78        Kumaraswamy Layout                              2               0   
80            Lingarajapuram                              2               0   
52                  Hulimavu                              2               0   
82   Mahadevapura, Bangalore                              2               0   
93            Nandini Layout                              2               0   
95           Padmanabhanagar                              2               0   
23                Carmelaram                              2               0   
73      Kodihalli, Bangalore                              2               0   
112  Shivajinagar, Bangalore                              2               0   
123                   Ulsoor                              2               0   
129               Vimanapura                              2               0   
107           Sadashivanagar                              2               0   

      Latitude  Longitude  
103  13.117880  77.559210  
62   12.781130  77.642580  
78   12.898190  77.559270  
80   13.005480  77.625970  
52   12.880640  77.601470  
82   12.994090  77.666330  
93   13.014810  77.538910  
95   12.918140  77.559400  
23   12.959697  77.571312  
73   12.966200  77.649820  
112  12.987200  77.604010  
123  12.989080  77.627950  
129  13.002540  77.667640  
107  13.014830  77.577710

#### Cluster 2

In [120]:
kl_merged.loc[kl_merged['Cluster Labels'] == 1]
#len(kl_merged.loc[kl_merged['Cluster Labels'] == 1])

Neighborhood  Vegetarian / Vegan Restaurant  Cluster Labels  \
110             Seshadripuram                              1               1   
106             Richmond Town                              1               1   
130                Vyalikaval                              1               1   
99                R. T. Nagar                              1               1   
113      Siddapura, Bangalore                              1               1   
90              Murugeshpalya                              1               1   
87                  Mathikere                              1               1   
83         Mahalakshmi Layout                              1               1   
117           Suddaguntepalya                              1               1   
125                   Varthur                              1               1   
127            Vidyaranyapura                              1               1   
1            Agara, Bangalore                              1               1   
131     Whitefield, Bangalore                              1               1   
67                    Kalkere                              1               1   
3                  Anjanapura                              1               1   
6                  BTM Layout                              1               1   
8    Bagalur, Bangalore Urban                              1               1   
9               Bahubalinagar                              1               1   
11                  Banaswadi                              1               1   
19                Bommasandra                              1               1   
32             Dollars Colony                              1               1   
34                    Ejipura                              1               1   
71                    Kengeri                              1               1   
35            Electronic City                              1               1   
60       Jayanagar, Bangalore                              1               1   
38    Gandhi Nagar, Bangalore                              1               1   
39            Gangamma Circle                              1               1   
54                Indiranagar                              1               1   
42                  Girinagar                              1               1   
45                 HBR Layout                              1               1   
43                  Gottigere                              1               1   

      Latitude  Longitude  
110  12.993550   77.57988  
106  12.962340   77.60123  
130  13.037920   77.61863  
99   13.024450   77.59590  
113  12.956130   77.73196  
90   12.955650   77.65335  
87   13.032350   77.55866  
83   13.016350   77.54481  
117  12.983890   77.65476  
125  12.943480   77.74703  
127  13.079270   77.55914  
1    12.842830   77.48759  
131  12.979380   77.73372  
67   13.034030   77.67511  
3    12.858110   77.55909  
6    13.027530   77.65049  
8    13.044710   77.55008  
9    12.922310   77.56988  
11   12.938980   77.57137  
19   12.993330   77.66123  
32   13.040250   77.56909  
34   12.946970   77.62559  
71   12.908700   77.48714  
35   12.845470   77.66430  
60   12.928720   77.58281  
38   13.026430   77.61774  
39   13.056825   77.54676  
54   13.030060   77.49526  
42   12.942790   77.54122  
45   12.943720   77.56120  
43   12.855680   77.58557

#### Cluster 3

In [121]:
kl_merged.loc[kl_merged['Cluster Labels'] == 2] 
#len(kl_merged.loc[kl_merged['Cluster Labels'] == 2] ) 

Neighborhood  Vegetarian / Vegan Restaurant  Cluster Labels  \
96   Palace Guttahalli                              3               2   
14           Bellandur                              3               2   
15      Bengaluru Pete                              3               2   
18        Bommanahalli                              3               2   
85        Marathahalli                              3               2   
104   Ramamurthy Nagar                              3               2   
37       Gandhi Bazaar                              3               2   
76         Koramangala                              3               2   

      Latitude  Longitude  
96   12.995508  77.574772  
14   12.960530  77.643850  
15   13.083010  77.547790  
18   12.817530  77.678790  
85   12.954660  77.707520  
104  13.023820  77.677850  
37   12.944780  77.572130  
76   12.920040  77.625460

#### Cluster 4

In [122]:
kl_merged.loc[kl_merged['Cluster Labels'] == 3] 
#len(kl_merged.loc[kl_merged['Cluster Labels'] == 3] ) #-There are only 2 neighborhoods with 4 restaurants

Neighborhood  Vegetarian / Vegan Restaurant  Cluster Labels  Latitude  \
81     Madiwala                              4               3  12.92052   
97       Peenya                              4               3  13.03185   

    Longitude  
81   77.62090  
97   77.52679

## Final observation
The analysis throws some intresting insight to the services available in various localities across Bangalore. Additionally it shows that there are a good number of vegan restaurants spread across the Bangalore city. Though the number is scattered across Bangalore city, couple of places where the Vegna restaurants can be targetted to open are places where there are one restaurants but they have a good number of IT folks. These places can be Electronic City, BTM Layout, Indira Nagar. It is also surprising to see that Peenya like place having maximum number of Vegan restuarants.